# Δέντρα αποφάσεων

Αν χρειάστηκε ποτέ να διαγνώσετε ένα πρόβλημα με μια συσκευή, ένα αυτοκίνητο ή έναν υπολογιστή, υπάρχει μεγάλη πιθανότητα να έχετε συναντήσει ένα διάγραμμα ροής αντιμετώπισης προβλημάτων. Ένα διάγραμμα ροής είναι μια δενδροειδής δομή ερωτήσεων ναι/όχι που σας καθοδηγεί μέσω κάποιας διαδικασίας με βάση τη συγκεκριμένη κατάσταση. 

Ένα δέντρο αποφάσεων είναι ουσιαστικά ένα διάγραμμα ροής για τη λήψη απόφασης σχετικά με τον τρόπο ταξινόμησης μιας παρατήρησης: αποτελείται από μια σειρά αποφάσεων ναι/όχι ή αν/αν, οι οποίες τελικά αντιστοιχίζουν κάθε παρατήρηση σε μια συγκεκριμένη πιθανότητα ή κλάση. Η σειρά των αποφάσεων ναι/όχι μπορεί να απεικονιστεί ως μια σειρά από κλαδιά που οδηγούν σε αποφάσεις ή "φύλλα" στο κάτω μέρος του δέντρου.

## Titanic dataset
![](https://miro.medium.com/max/600/0*CBDzZWhzCjBY2LhS.jpeg)

Ας δημιουργήσουμε το μοντέλο με βάση το φύλο στο [Titanic training set](https://www.kaggle.com/c/titanic/data) χρησιμοποιώντας δέντρα απόφασης στην Python. Πρώτα θα φορτώσουμε κάποιες βιβλιοθήκες και θα προεπεξεργαστούμε τα δεδομένα του Τιτανικού:

In [ ]:
import numpy as np
import pandas as pd

In [ ]:
# Load and prepare Titanic data

titanic_train = pd.read_csv("https://pastebin.com/raw/phdcr5FY")    # Read the training data

  
# Impute median Age for NA Age values
new_age_var = np.where(titanic_train["Age"].isnull(), # Logical check
                       28,                       # Value if check is true
                       titanic_train["Age"])     # Value if check is false

titanic_train["Age"] = new_age_var 

In [ ]:
titanic_train.head(10)

Στη συνέχεια, πρέπει να φορτώσουμε και να αρχικοποιήσουμε το μοντέλο δέντρου αποφάσεων του scikit-learn και στη συνέχεια να εκπαιδεύσουμε το μοντέλο χρησιμοποιώντας τη μεταβλητή sex:

## Decision Tree classifier 1

In [ ]:
from sklearn import tree
from sklearn import preprocessing

In [ ]:
# Initialize label encoder
label_encoder = preprocessing.LabelEncoder()

# Convert Sex variable to numeric
encoded_sex = label_encoder.fit_transform(titanic_train["Sex"])

# Initialize model
tree_model = tree.DecisionTreeClassifier()

# Train the model
tree_model.fit(X = pd.DataFrame(encoded_sex), 
               y = titanic_train["Survived"])

Σημειώστε τις default τιμές των παραμέτρων στο παραπάνω μοντέλο. Διαβάστε περισσότερα για αυτες [εδώ](http://scikit-learn.org/stable/modules/generated/sklearn.tree.DecisionTreeClassifier.html).

Τώρα ας δούμε μια οπτικοποίηση του δέντρου που δημιούργησε το μοντέλο:.

In [ ]:
# Save tree as dot file
with open("tree1.dot", 'w') as f:
     f = tree.export_graphviz(tree_model, 
                              feature_names=["Sex"], 
                              out_file=f)

In [ ]:
!apt update && apt install -y graphviz

In [ ]:
!dot -Tpng tree1.dot -o tree1.png -Gdpi=100

In [ ]:
!ls

In [ ]:
# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree1.png')

Το γράφημα του δέντρου μας δείχνει ότι αποτελείται από έναν μόνο κόμβο απόφασης που διαχωρίζει τα δεδομένα για τη μεταβλητή φύλο. Και τα 314 θηλυκά καταλήγουν σε έναν κόμβο φύλλων και τα 577 αρσενικά καταλήγουν σε έναν διαφορετικό κόμβο φύλλων.

Ας κάνουμε προβλέψεις με αυτό το δέντρο και ας δούμε έναν πίνακα με τα αποτελέσματα:

In [ ]:
# Get survival probability
preds = tree_model.predict_proba(X = pd.DataFrame(encoded_sex))

pd.crosstab(preds[:,0], titanic_train["Sex"])

**Αριστερό βέλος σημαίνει "Αληθές", δεξί βέλος σημαίνει "Λάθος". Στους κόμβους των φύλλων ο ταξινομητής επιλέγει την πλειοψηφική κλάση (αν υπάρχουν μη καθαρά φύλλα (gini>0), τότε υπάρχει σφάλμα ταξινόμησης).**

Ο πίνακας δείχνει ότι το δέντρο απόφασης κατάφερε να δημιουργήσει ένα απλό μοντέλο με βάση το φύλο, όπου αν είστε γυναίκα επιβάτης θα πνιγείτε με πιθανότητα 0,257962 και αν είστε άνδρας επιβάτης θα πνιγείτε με πιθανότητα 0,811092.

Ας δημιουργήσουμε ένα νέο δέντρο απόφασης που προσθέτει τη μεταβλητή κλάση επιβάτη και ας δούμε πώς αλλάζει τις προβλέψεις που προκύπτουν:

In [ ]:
# Make data frame of predictors
predictors = pd.DataFrame([encoded_sex, titanic_train["Pclass"]]).T

# Train the model
tree_model.fit(X = predictors, 
               y = titanic_train["Survived"])

Ας δούμε το νέο γράφο που δημιουργεί το νέο μοντέλο:

In [ ]:
with open("tree2.dot", 'w') as f:
     f = tree.export_graphviz(tree_model, 
                              feature_names=["Sex", "Class"], 
                              out_file=f)

In [ ]:
!dot -Tpng tree2.dot -o tree2.png -Gdpi=100

In [ ]:
# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree2.png')

Παρατηρήστε ότι με την προσθήκη μιας ακόμη μεταβλητής, το δέντρο γίνεται σημαντικά πιο πολύπλοκο. Τώρα έχει 6 κόμβους απόφασης, 6 κόμβους φύλλων και μέγιστο βάθος 3.

Ας κάνουμε προβλέψεις και ας δούμε έναν πίνακα με τα αποτελέσματα:

In [ ]:
# Get survival probability
preds = tree_model.predict_proba(X = predictors)

# Create a table of predictions by sex and class
pd.crosstab(preds[:,0], columns = [titanic_train["Pclass"], 
                                   titanic_train["Sex"]])

## Εξαγωγή κανόνων

Μπορούμε εύκολα να εξάγουμε τους κανόνες διασχίζοντας αναδρομικά το δένδρο


In [ ]:
def tree_to_pseudo(tree, feature_names):

	'''
	Outputs a decision tree model as if/then pseudocode
	
	Parameters:
	-----------
	tree: decision tree model
		The decision tree to represent as pseudocode
	feature_names: list
		The feature names of the dataset used for building the decision tree
	'''

	left = tree.tree_.children_left
	right = tree.tree_.children_right
	threshold = tree.tree_.threshold
	features = [feature_names[i] for i in tree.tree_.feature]
	value = tree.tree_.value

	def recurse(left, right, threshold, features, node, depth=0):
		indent = "  " * depth
		if (threshold[node] != -2):
			print(indent,"if ( " + features[node] + " <= " + str(threshold[node]) + " ) {")
			if left[node] != -1:
				recurse (left, right, threshold, features, left[node], depth+1)
				print(indent,"} else {")
				if right[node] != -1:
					recurse (left, right, threshold, features, right[node], depth+1)
				print(indent,"}")
		else:
			print(indent,"return " + str(value[node]))

	recurse(left, right, threshold, features, 0)

In [ ]:
tree_to_pseudo(tree_model, ["Sex", "Class"])

Ο ταξινονητής στα φύλλα προβλέπει την πλειοψηφική κλάση (ή κάποια σε περίπτωση ισοπαλίας). Στην πρώτη θέση είναι survive="no" και η δεύτερη survive="yes". Μπορεί να έχουμε σφάλμα στο training set μπορεί και να μην έχουμε. Στη δεύτερη περίπτωση, αν και διαισθητικά το δένδρο που προκύπτει μοιάζει καλύτερο (μηδενικό εμπειρικό ρίσκο), πρέπει να θυμόμαστε ότι μπορεί να έχουμε πέσει σε μια κακή υπόθεση.

## Ψηλότερα δένδρα (περισσότερες μεταβλητές)


Notice that the more complex model still predicts a higher survival rate for women than men, but women in third class only have a 50% predicted death probability while women in first class are predicted to die less than 5% of the time.


The more variables you add to a decision tree, the more yes/no decisions it can make, resulting in a deeper, more complex tree. Adding too much complexity to a decision tree, however, makes it prone to overfitting the training data, which can lead to poor generalization to unseen data. Let's investigate by creating a larger tree with a few more variables:

In [ ]:
predictors = pd.DataFrame([encoded_sex,
                           titanic_train["Pclass"],
                           titanic_train["Age"],
                           titanic_train["Fare"]]).T

# Initialize model with maximum tree depth set to 8
tree_model = tree.DecisionTreeClassifier(max_depth = 8)

tree_model.fit(X = predictors, 
               y = titanic_train["Survived"])

In [ ]:
with open("tree3.dot", 'w') as f:
     f = tree.export_graphviz(tree_model, 
                              feature_names=["Sex", "Class","Age","Fare"], 
                              out_file=f)

In [ ]:
!dot -Tpng tree3.dot -o tree3.png -Gdpi=90

In [ ]:
# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree3.png')


Η παραπάνω εικόνα δείχνει πόσο πολύπλοκα μπορούν να γίνουν τα δέντρα αποφάσεων όταν αρχίσετε να προσθέτετε περισσότερες επεξηγηματικές μεταβλητές. Μπορείτε να ελέγξετε την πολυπλοκότητα του δέντρου τροποποιώντας ορισμένες από τις προεπιλεγμένες παραμέτρους της συνάρτησης δέντρου αποφάσεων. 

Στα φύλλο του δέντρου η απόφαση γίνεται με την πλειοψηφία: άν έχουμε δηλαδή για παράδειγμα "1 3"  (ένας πνίγηκε - τρεις σώθηκαν, σύνολο 4) o ταξινομητής, για όσα δείγματα πληρούν τις συνθήκες του δέντρου μέχρι να φτάσουμε στο συγκεκριμένο φύλλο, θα αποφασίζει "σώθηκε" δλδ κλάση 1 (η κλάση 0 είναι η "πνίγηκε"). Αυτό σημαίνει οτι, στο training set θα κάνει και ένα σφάλμα στα συγκεκριμένο φύλλοι για τον 1 του φύλλου από τους 4 που πνίγηκε. Όταν το gini index είναι >0 στα φύλλα, σημαίνει ότι υπάρχει λάθος ταξινόμησης στην εκπαίδευση. Το ποια σφάλματα θα γίνουν στη φάση της αποτίμησης (test) δεν το γνωρίζουμε γιατί δεν έχουμε δει ακόμα τα δείγματα του test set. Ωστόσο οι αποφάσεις του δέντρου με βάση τις συνθήκες των εσωτεριών κόμβων και για το test θαείναι αυτές ακριβώς που καθορίστηκαν στην εκπαίδευση (στο train set).

Ας ελέγξουμε την ακρίβεια αυτού του μοντέλου δέντρου αποφάσεων στα δεδομένα εκπαίδευσης:

In [ ]:
tree_model.score(X = predictors, 
                 y = titanic_train["Survived"])

Το μοντέλο είναι σχεδόν 89% πιστό στα δεδομένα εκπαίδευσης, αλλά πώς τα καταφέρνει με άγνωστα δεδομένα; 

Το σύνολο δεδομένων Titanic είναι ακόμα ένας ανοιχτός διαγωνισμός του Kaggle, οπότε οι ετικέτες ελέγχου είναι άγνωστες. Μπορείτε να υποβάλετε τις προβλέψεις σας για να λάβετε ένα αποτέλεσμα ορθότητας και την κατάταξή σας.

## Download των γραφημάτων από το Colab


In [ ]:
!ls

Για να κατεβάσουμε τοπικά τις εικόνες των δένδρων (.png) μπορούμε να κάνουμε το ακόλουθο:

In [ ]:
from google.colab import files
files.download('tree1.png')
files.download('tree2.png')
files.download('tree3.png')